In [1]:
import os
import shutil
import torch
import torch.nn as nn
import sys
import random
import numpy as np
from models.cifar_quant import cifar10_quantqf
import models.testset as ts
from models.train import *
import pickle
from models.tests import TestBench as TB
from models.quant_back import Conv2dQ, Conv2dQB

def dump_vars(filename, **vars):
    with open(filename, 'wb') as f:
        pickle.dump(vars, f)

if not os.path.exists('result'):
    os.makedirs('result')


cuda_device = 0
os.environ['CUBLAS_WORKSPACE_CONFIG'] = ':4096:8'
torch.manual_seed(0)
random.seed(0)
np.random.seed(0)
torch.use_deterministic_algorithms(True)
torch.backends.cudnn.deterministic = True
torch.cuda.set_device(cuda_device)
tsname = 'R32_LU_4X'

Files already downloaded and verified
Files already downloaded and verified


In [11]:
params = [
      {'lr': 2e-3, 'nhist': 1, 'epoch': 5},
      {'lr': 2e-3, 'nhist': 5, 'epoch': 10},
      {'lr': 4e-4, 'nhist': 5, 'epoch': 20},
      {'lr': 2e-3, 'nhist': 10, 'epoch': 100},
      {'lr': 2e-3, 'nhist': 10, 'epoch': 200}
]
fbits = [2, 3, 4]
gbits = [2, 3, 4, 5, 6, 7]
cl = {'Mean': lambda x: x.abs().mean(), '2xMean': lambda x: x.abs().mean() * 2, '3xMean': lambda x: x.abs().mean() * 3}
#      'Max/4': lambda x: x.abs().max() / 4, 'Max/2': lambda x: x.abs().max(), '.75Max': lambda x: x.abs().max() * 0.75, 'Max': lambda x: x.abs().max()} 

oparams = {'weight_decay': 1e-4, 'momentum': 0.9} # {'M': {'weight_decay': 1e-4, 'momentum': 0.9}, 'N': {'weight_decay': 0, 'momentum': 0}}
#epochs = [10]
best_prec = 0
criterion = nn.CrossEntropyLoss().cuda()
loaded = torch.load(f'result/CIFAR10_ORG/model_best.pth.tar', map_location={'cuda:1': f'cuda:{cuda_device}'})


In [12]:


def getopt(x, *kargs, **kwargs):
    return torch.optim.SGD(x.parameters(), **kwargs)

tbs = []


for p in params:
    for f in fbits:
        for g in gbits:
            for c in cl:
                TBx = TB(f'{f}/{g}/{c}/{p["epoch"]}', validate_training_sep, criterion,
                        getopt=lambda x, y, lr=p['lr'], p=oparams: getopt(x, lr=lr, **p), nhist=p['nhist'], n_epoch=p['epoch'], trf_eval=trf_norm, trf_train=trf_train_norm)
                TBx.f = f
                TBx.g = g
                TBx.c = cl[c]
                tbs.append(TBx)


In [13]:

for tb in tbs:
    model = cifar10_quantqf()
    model.cuda()
    model.load_state_dict(loaded['state_dict'])
    func = Conv2dQB(4, 3, tb.f, tb.f-1, tb.g, 0, tb.c)
    with torch.no_grad():
        model.recursive_do('update_func', func)
    result[tb.name] = tb.run(ts.test_pld_sets[tsname], model)
    del model

Sequential(
  (0): QuantConv2df(3, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (1): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (2): ReLU()
  (3): QuantConv2df(128, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (4): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (5): ReLU()
  (6): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (7): QuantConv2df(128, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (8): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (9): ReLU()
  (10): QuantConv2df(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (11): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=False, track_running_stats=True)
  (12): ReLU()
  (13): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (14): QuantConv2df(256, 512, kernel_

Time 50.41608667373657	Epoch: 100	Loss 0.0860	Prec 96.797
Time 50.90051054954529	Epoch: 101	Loss 0.0822	Prec 97.188
Time 51.399641275405884	Epoch: 102	Loss 0.0860	Prec 97.266
Time 51.888298749923706	Epoch: 103	Loss 0.0765	Prec 97.734
Time 52.36861062049866	Epoch: 104	Loss 0.0914	Prec 97.188
Time 52.86581563949585	Epoch: 105	Loss 0.0641	Prec 98.203
Time 53.37232184410095	Epoch: 106	Loss 0.1280	Prec 96.250
Time 53.87816882133484	Epoch: 107	Loss 0.0641	Prec 98.594
Time 54.387672662734985	Epoch: 108	Loss 0.0760	Prec 97.578
Time 54.894770860672	Epoch: 109	Loss 0.0676	Prec 98.203
Time 55.4015691280365	Epoch: 110	Loss 0.0619	Prec 98.281
Time 55.893155336380005	Epoch: 111	Loss 0.0648	Prec 98.516
Time 56.37694692611694	Epoch: 112	Loss 0.0595	Prec 98.281
Time 56.862316370010376	Epoch: 113	Loss 0.0649	Prec 98.516
Time 57.360461473464966	Epoch: 114	Loss 0.0443	Prec 98.828
Time 57.839317083358765	Epoch: 115	Loss 0.0609	Prec 98.359
Time 58.34494471549988	Epoch: 116	Loss 0.0748	Prec 97.812
Time 58.83

Time 14.644067764282227	Epoch: 28	Loss 0.2637	Prec 91.172
Time 15.140114784240723	Epoch: 29	Loss 0.3003	Prec 91.250
Time 15.638047695159912	Epoch: 30	Loss 0.2521	Prec 91.719
Time 16.141226530075073	Epoch: 31	Loss 0.2411	Prec 92.188
Time 16.644917726516724	Epoch: 32	Loss 0.2539	Prec 92.422
Time 17.148818254470825	Epoch: 33	Loss 0.2476	Prec 92.812
Time 17.65321373939514	Epoch: 34	Loss 0.2228	Prec 92.734
Time 18.15618395805359	Epoch: 35	Loss 0.1845	Prec 93.438
Time 18.655943155288696	Epoch: 36	Loss 0.1705	Prec 94.688
Time 19.18323588371277	Epoch: 37	Loss 0.2092	Prec 94.297
Time 19.672064065933228	Epoch: 38	Loss 0.1534	Prec 95.234
Time 20.160900831222534	Epoch: 39	Loss 0.2090	Prec 93.203
Time 20.658445596694946	Epoch: 40	Loss 0.2095	Prec 93.906
Time 21.150208950042725	Epoch: 41	Loss 0.1610	Prec 94.688
Time 21.64836096763611	Epoch: 42	Loss 0.1481	Prec 95.938
Time 22.13621950149536	Epoch: 43	Loss 0.1453	Prec 95.938
Time 22.628004789352417	Epoch: 44	Loss 0.1598	Prec 95.156
Time 23.12377619743

Time 85.62873315811157	Epoch: 171	Loss 0.0187	Prec 99.844
Time 86.12561702728271	Epoch: 172	Loss 0.0163	Prec 100.000
Time 86.61886310577393	Epoch: 173	Loss 0.0191	Prec 99.844
Time 87.11063408851624	Epoch: 174	Loss 0.0198	Prec 99.688
Time 87.60166358947754	Epoch: 175	Loss 0.0165	Prec 99.844
Time 88.10342168807983	Epoch: 176	Loss 0.0260	Prec 99.453
Time 88.59069895744324	Epoch: 177	Loss 0.0142	Prec 99.922
Time 89.08017063140869	Epoch: 178	Loss 0.0206	Prec 99.844
Time 89.58398079872131	Epoch: 179	Loss 0.0251	Prec 99.375
Time 90.07469844818115	Epoch: 180	Loss 0.0120	Prec 100.000
Time 90.5817494392395	Epoch: 181	Loss 0.0204	Prec 99.531
Time 91.0919840335846	Epoch: 182	Loss 0.0170	Prec 99.922
Time 91.5830328464508	Epoch: 183	Loss 0.0191	Prec 99.922
Time 92.08307337760925	Epoch: 184	Loss 0.0171	Prec 100.000
Time 92.57563638687134	Epoch: 185	Loss 0.0194	Prec 99.609
Time 93.06187343597412	Epoch: 186	Loss 0.0138	Prec 100.000
Time 93.55198693275452	Epoch: 187	Loss 0.0206	Prec 99.922
Time 94.03816

Time 50.43719983100891	Epoch: 100	Loss 0.0202	Prec 100.000
Time 50.9375433921814	Epoch: 101	Loss 0.0267	Prec 99.688
Time 51.433478355407715	Epoch: 102	Loss 0.0257	Prec 99.609
Time 51.93301343917847	Epoch: 103	Loss 0.0293	Prec 99.766
Time 52.423452377319336	Epoch: 104	Loss 0.0307	Prec 99.688
Time 52.95093536376953	Epoch: 105	Loss 0.0288	Prec 99.609
Time 53.4492404460907	Epoch: 106	Loss 0.0290	Prec 99.531
Time 53.951924324035645	Epoch: 107	Loss 0.0235	Prec 99.844
Time 54.45081162452698	Epoch: 108	Loss 0.0216	Prec 99.766
Time 54.947402000427246	Epoch: 109	Loss 0.0243	Prec 99.844
Time 55.44122505187988	Epoch: 110	Loss 0.0168	Prec 100.000
Time 55.93777871131897	Epoch: 111	Loss 0.0315	Prec 99.297
Time 56.42868399620056	Epoch: 112	Loss 0.0192	Prec 99.688
Time 56.91909646987915	Epoch: 113	Loss 0.0166	Prec 100.000
Time 57.41494965553284	Epoch: 114	Loss 0.0204	Prec 99.688
Time 57.93422245979309	Epoch: 115	Loss 0.0218	Prec 99.922
Time 58.440415143966675	Epoch: 116	Loss 0.0154	Prec 100.000
Time 58

...

Time 76.39729022979736	Epoch: 154	Loss 0.0103	Prec 100.000
Time 76.88500785827637	Epoch: 155	Loss 0.0132	Prec 100.000
Time 77.39877772331238	Epoch: 156	Loss 0.0161	Prec 99.922
Time 77.89758777618408	Epoch: 157	Loss 0.0104	Prec 100.000
Time 78.39344668388367	Epoch: 158	Loss 0.0104	Prec 100.000
Time 78.8874089717865	Epoch: 159	Loss 0.0112	Prec 100.000
Time 79.38966774940491	Epoch: 160	Loss 0.0128	Prec 99.922
Time 79.8785753250122	Epoch: 161	Loss 0.0122	Prec 100.000
Time 80.36189556121826	Epoch: 162	Loss 0.0124	Prec 99.922
Time 80.84923648834229	Epoch: 163	Loss 0.0184	Prec 99.922
Time 81.33975601196289	Epoch: 164	Loss 0.0131	Prec 100.000
Time 81.82509303092957	Epoch: 165	Loss 0.0106	Prec 100.000
Time 82.30915403366089	Epoch: 166	Loss 0.0128	Prec 100.000
Time 82.79237341880798	Epoch: 167	Loss 0.0115	Prec 99.922
Time 83.31017589569092	Epoch: 168	Loss 0.0101	Prec 100.000
Time 83.79819130897522	Epoch: 169	Loss 0.0108	Prec 100.000
Time 84.28173899650574	Epoch: 170	Loss 0.0124	Prec 100.000
Time

Time 40.75585675239563	Epoch: 82	Loss 0.0309	Prec 99.688
Time 41.24032521247864	Epoch: 83	Loss 0.0283	Prec 99.844
Time 41.72644782066345	Epoch: 84	Loss 0.0388	Prec 99.531
Time 42.21154522895813	Epoch: 85	Loss 0.0399	Prec 99.297
Time 42.696195125579834	Epoch: 86	Loss 0.0287	Prec 99.844
Time 43.18170118331909	Epoch: 87	Loss 0.0285	Prec 99.766
Time 43.6633677482605	Epoch: 88	Loss 0.0360	Prec 99.375
Time 44.14969491958618	Epoch: 89	Loss 0.0248	Prec 99.766
Time 44.63546824455261	Epoch: 90	Loss 0.0293	Prec 99.844
Time 45.116384983062744	Epoch: 91	Loss 0.0294	Prec 99.688
Time 45.602240800857544	Epoch: 92	Loss 0.0344	Prec 99.375
Time 46.11021161079407	Epoch: 93	Loss 0.0388	Prec 99.531
Time 46.59189581871033	Epoch: 94	Loss 0.0313	Prec 99.297
Time 47.08142876625061	Epoch: 95	Loss 0.0216	Prec 99.844
Time 47.562912464141846	Epoch: 96	Loss 0.0275	Prec 99.844
Time 48.04906916618347	Epoch: 97	Loss 0.0293	Prec 99.609
Time 48.536810874938965	Epoch: 98	Loss 0.0190	Prec 99.922
Time 49.030402421951294	Epo

Time 5.098767995834351	Epoch: 9	Loss 0.4196	Prec 86.172
Time 5.580307245254517	Epoch: 10	Loss 0.3547	Prec 88.359
Time 6.061481475830078	Epoch: 11	Loss 0.3831	Prec 86.875
Time 6.542436122894287	Epoch: 12	Loss 0.3031	Prec 89.922
Time 7.026916742324829	Epoch: 13	Loss 0.3886	Prec 88.516
Time 7.508874416351318	Epoch: 14	Loss 0.3130	Prec 89.609
Time 7.989593505859375	Epoch: 15	Loss 0.2613	Prec 90.703
Time 8.470671892166138	Epoch: 16	Loss 0.2817	Prec 90.078
Time 8.952325820922852	Epoch: 17	Loss 0.2115	Prec 92.031
Time 9.439272165298462	Epoch: 18	Loss 0.2032	Prec 93.672
Time 9.927489995956421	Epoch: 19	Loss 0.2296	Prec 92.422
Time 10.418782234191895	Epoch: 20	Loss 0.2237	Prec 92.891
Time 10.91367220878601	Epoch: 21	Loss 0.2463	Prec 92.266
Time 11.414261102676392	Epoch: 22	Loss 0.1966	Prec 93.984
Time 11.902684688568115	Epoch: 23	Loss 0.1289	Prec 96.641
Time 12.407447814941406	Epoch: 24	Loss 0.1532	Prec 95.312
Time 12.891315221786499	Epoch: 25	Loss 0.1226	Prec 96.719
Time 13.379731178283691	Epo

Time 74.78597640991211	Epoch: 151	Loss 0.0206	Prec 100.000
Time 75.27115297317505	Epoch: 152	Loss 0.0192	Prec 99.922
Time 75.75358533859253	Epoch: 153	Loss 0.0160	Prec 99.922
Time 76.24624609947205	Epoch: 154	Loss 0.0243	Prec 99.609
Time 76.73951625823975	Epoch: 155	Loss 0.0205	Prec 99.844
Time 77.22993421554565	Epoch: 156	Loss 0.0176	Prec 99.922
Time 77.72446537017822	Epoch: 157	Loss 0.0174	Prec 99.844
Time 78.21887969970703	Epoch: 158	Loss 0.0128	Prec 100.000
Time 78.71068572998047	Epoch: 159	Loss 0.0137	Prec 100.000
Time 79.20860004425049	Epoch: 160	Loss 0.0161	Prec 99.922
Time 79.70212006568909	Epoch: 161	Loss 0.0164	Prec 100.000
Time 80.20802187919617	Epoch: 162	Loss 0.0135	Prec 99.922
Time 80.71204566955566	Epoch: 163	Loss 0.0171	Prec 99.922
Time 81.20796728134155	Epoch: 164	Loss 0.0153	Prec 100.000
Time 81.70936465263367	Epoch: 165	Loss 0.0162	Prec 99.922
Time 82.20638132095337	Epoch: 166	Loss 0.0162	Prec 99.844
Time 82.69899916648865	Epoch: 167	Loss 0.0133	Prec 99.922
Time 83.1

Time 34.16112542152405	Epoch: 80	Loss 0.0288	Prec 99.712
Time 34.58038139343262	Epoch: 81	Loss 0.0287	Prec 99.615
Time 35.00521945953369	Epoch: 82	Loss 0.0339	Prec 99.423
Time 35.42767095565796	Epoch: 83	Loss 0.0261	Prec 99.904
Time 35.85279297828674	Epoch: 84	Loss 0.0240	Prec 99.904
Time 36.27493906021118	Epoch: 85	Loss 0.0478	Prec 99.327
Time 36.70030879974365	Epoch: 86	Loss 0.0315	Prec 99.808
Time 37.11860537528992	Epoch: 87	Loss 0.0326	Prec 99.327
Time 37.53926396369934	Epoch: 88	Loss 0.0293	Prec 99.615
Time 37.95775032043457	Epoch: 89	Loss 0.0268	Prec 99.808
Time 38.37856841087341	Epoch: 90	Loss 0.0297	Prec 99.712
Time 38.80173468589783	Epoch: 91	Loss 0.0182	Prec 100.000
Time 39.22046160697937	Epoch: 92	Loss 0.0305	Prec 99.615
Time 39.63772249221802	Epoch: 93	Loss 0.0227	Prec 100.000
Time 40.05417275428772	Epoch: 94	Loss 0.0277	Prec 99.904
Time 40.47054052352905	Epoch: 95	Loss 0.0206	Prec 99.904
Time 40.90094995498657	Epoch: 96	Loss 0.0214	Prec 99.808
Time 41.32098126411438	Epoch:

In [14]:
dump_vars('Quant_Incremental_Parameter_Sweep_Mean.txt', result=result)

In [15]:
{x: result[x][0] for x in result}

{'2/2/Mean/5': 76.21,
 '2/2/2xMean/5': 76.19,
 '2/2/3xMean/5': 76.09,
 '2/3/Mean/5': 75.87,
 '2/3/2xMean/5': 75.98,
 '2/3/3xMean/5': 76.16,
 '2/4/Mean/5': 76.23,
 '2/4/2xMean/5': 76.25,
 '2/4/3xMean/5': 76.13,
 '2/5/Mean/5': 76.09,
 '2/5/2xMean/5': 76.11,
 '2/5/3xMean/5': 76.07,
 '2/6/Mean/5': 75.94,
 '2/6/2xMean/5': 76.13,
 '2/6/3xMean/5': 76.23,
 '2/7/Mean/5': 75.8,
 '2/7/2xMean/5': 76.19,
 '2/7/3xMean/5': 76.11,
 '3/2/Mean/5': 76.23,
 '3/2/2xMean/5': 76.03,
 '3/2/3xMean/5': 76.2,
 '3/3/Mean/5': 76.25,
 '3/3/2xMean/5': 76.18,
 '3/3/3xMean/5': 76.33,
 '3/4/Mean/5': 76.19,
 '3/4/2xMean/5': 76.34,
 '3/4/3xMean/5': 76.47,
 '3/5/Mean/5': 75.96,
 '3/5/2xMean/5': 76.05,
 '3/5/3xMean/5': 76.58,
 '3/6/Mean/5': 76.34,
 '3/6/2xMean/5': 76.3,
 '3/6/3xMean/5': 76.23,
 '3/7/Mean/5': 76.33,
 '3/7/2xMean/5': 76.28,
 '3/7/3xMean/5': 76.46,
 '4/2/Mean/5': 76.26,
 '4/2/2xMean/5': 76.41,
 '4/2/3xMean/5': 76.55,
 '4/3/Mean/5': 76.2,
 '4/3/2xMean/5': 76.45,
 '4/3/3xMean/5': 76.37,
 '4/4/Mean/5': 76.53,
 '